In [1]:
import time
import logging
import re
import random
import gc
import numpy as np
import pandas as pd
import torch
import evaluate

from datasets import Dataset, DatasetDict, load_from_disk
from transformers import (
    AutoModelForSeq2SeqLM,
    AutoTokenizer,
    TrainingArguments,
    Trainer,
    GenerationConfig,
    BitsAndBytesConfig,
)
from transformers.trainer_callback import EarlyStoppingCallback
from peft import LoraConfig, get_peft_model, prepare_model_for_kbit_training

In [2]:
# Enable cudnn benchmark for fixed input sizes (can speed up computation)
torch.backends.cudnn.benchmark = True

# Set device to RTX 4090
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device)

cuda


In [3]:
random.seed(42)
np.random.seed(42)
torch.manual_seed(42)
if torch.cuda.is_available():
    torch.cuda.manual_seed_all(42)

In [4]:
def clear_memory():
    gc.collect()
    torch.cuda.empty_cache()

In [5]:
logging.basicConfig(
    level=logging.INFO,
    format="%(asctime)s - %(levelname)s - %(message)s",
)
logger = logging.getLogger(__name__)

In [6]:
def preprocess(text: str) -> str:
    """Remove extra whitespaces and newlines from a text string."""
    if not isinstance(text, str):
        return ""
    return re.sub(r'\s+', ' ', text.replace('\n', ' ')).strip()

def clean_df(df, rename=None, drop=None, select=None):
    """
    Clean and rename dataframe columns:
      - drop: list of columns to drop
      - rename: dict mapping old column names to new names
      - select: list of columns to keep in final order
    """
    if drop:
        df = df.drop(columns=drop, errors='ignore')
    if rename:
        df = df.rename(columns=rename)
    for col in ['query', 'context', 'response']:
        if col in df.columns:
            df[col] = df[col].apply(preprocess)
    if select:
        df = df[select]
    return df

In [7]:
logger.info("Loading raw datasets from various sources...")

# Load datasets
df1 = pd.read_json("hf://datasets/Clinton/Text-to-sql-v1/texttosqlv2.jsonl", lines=True)
df2 = pd.read_json("hf://datasets/b-mc2/sql-create-context/sql_create_context_v4.json")
df3 = pd.read_parquet("hf://datasets/gretelai/synthetic_text_to_sql/synthetic_text_to_sql_train.snappy.parquet")
df4 = pd.read_json("hf://datasets/knowrohit07/know_sql/know_sql_val3{ign}.json")

# Clean and rename columns to unify to 'query', 'context', 'response'
df1 = clean_df(df1, rename={'instruction': 'query', 'input': 'context'}, drop=['source', 'text'])
df2 = clean_df(df2, rename={'question': 'query', 'answer': 'response'})
df3 = clean_df(df3, rename={'sql_prompt': 'query', 'sql_context': 'context', 'sql': 'response'},
                select=['query', 'context', 'response'])
df4 = clean_df(df4, rename={'question': 'query', 'answer': 'response'})

# Concatenate all DataFrames
final_df = pd.concat([df1, df2, df3, df4], ignore_index=True)
logger.info("Total rows before dropping duplicates: %d", len(final_df))

# Force correct column order and drop rows with missing fields
final_df = final_df[['query', 'context', 'response']]
final_df = final_df.dropna(subset=['query', 'context', 'response'])
final_df = final_df.drop_duplicates()
logger.info("Total rows after dropping duplicates: %d", len(final_df))

2025-03-19 14:56:53,295 - INFO - Loading raw datasets from various sources...
2025-03-19 14:57:25,655 - INFO - Total rows before dropping duplicates: 490241
2025-03-19 14:57:27,208 - INFO - Total rows after dropping duplicates: 440785


In [8]:
tokenizer = AutoTokenizer.from_pretrained("google/flan-t5-base")

max_length_prompt = 500
max_length_response = 250

def tokenize_length_filter(row):
    start_prompt = "Context:\n"
    middle_prompt = "\n\nQuery:\n"
    end_prompt = "\n\nResponse:\n"
    
    # Construct the prompt as used in the tokenize_function
    prompt = f"{start_prompt}{row['context']}{middle_prompt}{row['query']}{end_prompt}"
    
    # Encode without truncation to get the full token count
    prompt_tokens = tokenizer.encode(prompt, add_special_tokens=True, truncation=False)
    response_tokens = tokenizer.encode(row['response'], add_special_tokens=True, truncation=False)
    
    return len(prompt_tokens) <= max_length_prompt and len(response_tokens) <= max_length_response

final_df = final_df[final_df.apply(tokenize_length_filter, axis=1)]
logger.info("Total rows after filtering by token length (prompt <= %d and response <= %d tokens): %d", 
            max_length_prompt, max_length_response, len(final_df))


Token indices sequence length is longer than the specified maximum sequence length for this model (1113 > 512). Running this sequence through the model will result in indexing errors
2025-03-19 15:01:13,787 - INFO - Total rows after filtering by token length (prompt <= 500 and response <= 250 tokens): 398481


In [9]:
logger.info("Sample from filtered final_df:\n%s", final_df.head(3))
clear_memory()

2025-03-19 15:01:13,794 - INFO - Sample from filtered final_df:
                                               query  \
0           Name the home team for carlton away team   
1  what will the population of Asia be when Latin...   
2  How many faculty members do we have for each g...   

                                             context  \
0  CREATE TABLE table_name_77 ( home_team VARCHAR...   
1  CREATE TABLE table_22767 ( "Year" real, "World...   
2  CREATE TABLE Student ( StuID INTEGER, LName VA...   

                                            response  
0  SELECT home_team FROM table_name_77 WHERE away...  
1  SELECT "Asia" FROM table_22767 WHERE "Latin Am...  
2  SELECT Sex, COUNT(*) FROM Faculty GROUP BY Sex...  


In [10]:
def split_dataframe(df, train_frac=0.85, test_frac=0.1, val_frac=0.05):
    n = len(df)
    train_end = int(n * train_frac)
    test_end = train_end + int(n * test_frac)
    train_df = df.iloc[:train_end].reset_index(drop=True)
    test_df = df.iloc[train_end:test_end].reset_index(drop=True)
    val_df = df.iloc[test_end:].reset_index(drop=True)
    return train_df, test_df, val_df

train_df, test_df, val_df = split_dataframe(final_df)
logger.info("Final split sizes: Train: %d, Test: %d, Validation: %d", len(train_df), len(test_df), len(val_df))

# Convert splits to Hugging Face Datasets
train_dataset = Dataset.from_pandas(train_df)
test_dataset = Dataset.from_pandas(test_df)
val_dataset = Dataset.from_pandas(val_df)

dataset = DatasetDict({
    'train': train_dataset,
    'test': test_dataset,
    'validation': val_dataset
})

dataset.save_to_disk("merged_dataset")
logger.info("Merged and Saved Dataset Successfully!")
logger.info("Dataset summary: %s", dataset)
clear_memory()

2025-03-19 15:01:14,006 - INFO - Final split sizes: Train: 338708, Test: 39848, Validation: 19925


Saving the dataset (0/1 shards):   0%|          | 0/338708 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/39848 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/19925 [00:00<?, ? examples/s]

2025-03-19 15:01:15,490 - INFO - Merged and Saved Dataset Successfully!
2025-03-19 15:01:15,497 - INFO - Dataset summary: DatasetDict({
    train: Dataset({
        features: ['query', 'context', 'response'],
        num_rows: 338708
    })
    test: Dataset({
        features: ['query', 'context', 'response'],
        num_rows: 39848
    })
    validation: Dataset({
        features: ['query', 'context', 'response'],
        num_rows: 19925
    })
})


In [11]:
dataset = load_from_disk("merged_dataset")
logger.info("Reloaded dataset from disk. Example from test split:\n%s", dataset['test'][0])

model_name = "google/flan-t5-base"
tokenizer = AutoTokenizer.from_pretrained(model_name)

def tokenize_function(batch: dict) -> dict:
    """
    Tokenizes a batch of examples for T5 fine-tuning.
    Constructs a prompt in the format:
      Context:
      <context>
      
      Query:
      <query>
      
      Response:
    """
    start_prompt = "Context:\n"
    middle_prompt = "\n\nQuery:\n"
    end_prompt = "\n\nResponse:\n"

    prompts = [
        f"{start_prompt}{ctx}{middle_prompt}{qry}{end_prompt}"
        for ctx, qry in zip(batch['context'], batch['query'])
    ]

    tokenized_inputs = tokenizer(
        prompts,
        padding="max_length",
        truncation=True,
        max_length=512
    )
    tokenized_labels = tokenizer(
        batch['response'],
        padding="max_length",
        truncation=True,
        max_length=256
    )
    labels = [
        [-100 if token == tokenizer.pad_token_id else token for token in seq]
        for seq in tokenized_labels['input_ids']
    ]

    batch['input_ids'] = tokenized_inputs['input_ids']
    batch['attention_mask'] = tokenized_inputs['attention_mask']
    batch['labels'] = labels
    return batch

try:
    tokenized_datasets = load_from_disk("tokenized_datasets")
    logger.info("Loaded Tokenized Dataset from disk.")
except Exception as e:
    logger.info("Tokenized dataset not found. Creating a new one...")
    tokenized_datasets = dataset.map(
        tokenize_function,
        batched=True,
        remove_columns=['query', 'context', 'response'],
        num_proc=8
    )
    tokenized_datasets.save_to_disk("tokenized_datasets")
    logger.info("Tokenized and Saved Dataset.")

tokenized_datasets.set_format("torch")

logger.info("Final tokenized dataset splits: %s", tokenized_datasets.keys())
logger.info("Sample tokenized record from train split:\n%s", tokenized_datasets['train'][0])

2025-03-19 15:01:15,843 - INFO - Reloaded dataset from disk. Example from test split:
{'query': "Show the name and type of military cyber commands in the 'Military_Cyber_Commands' table.", 'context': "CREATE SCHEMA IF NOT EXISTS defense_security;CREATE TABLE IF NOT EXISTS defense_security.Military_Cyber_Commands (id INT PRIMARY KEY, command_name VARCHAR(255), type VARCHAR(255));INSERT INTO defense_security.Military_Cyber_Commands (id, command_name, type) VALUES (1, 'USCYBERCOM', 'Defensive Cyber Operations'), (2, 'JTF-CND', 'Offensive Cyber Operations'), (3, '10th Fleet', 'Network Warfare');", 'response': 'SELECT command_name, type FROM defense_security.Military_Cyber_Commands;'}
2025-03-19 15:01:16,155 - INFO - Loaded Tokenized Dataset from disk.
2025-03-19 15:01:16,159 - INFO - Final tokenized dataset splits: dict_keys(['train', 'test', 'validation'])
2025-03-19 15:01:16,167 - INFO - Sample tokenized record from train split:
{'input_ids': tensor([ 1193,  6327,    10,   205,  4386,  6

In [12]:
model_name = 'google/flan-t5-base'
tokenizer = AutoTokenizer.from_pretrained(model_name)
original_model = AutoModelForSeq2SeqLM.from_pretrained(model_name, torch_dtype=torch.bfloat16)
original_model = original_model.to(device)

index = 0
query = dataset['test'][index]['query']
context = dataset['test'][index]['context']
response = dataset['test'][index]['response']

prompt = f"""Context:
{context}

Query:
{query}

Response:
"""
inputs = tokenizer(prompt, return_tensors='pt').to(device)
baseline_output = tokenizer.decode(
    original_model.generate(
        inputs["input_ids"],
        max_new_tokens=200,
    )[0],
    skip_special_tokens=True
)
dash_line = '-' * 100
print(dash_line)
print(f'INPUT PROMPT:\n{prompt}')
print(dash_line)
print(f'BASELINE HUMAN ANSWER:\n{response}\n')
print(dash_line)
print(f'MODEL GENERATION - ZERO SHOT:\n{baseline_output}')
clear_memory()

----------------------------------------------------------------------------------------------------
INPUT PROMPT:
Context:
CREATE SCHEMA IF NOT EXISTS defense_security;CREATE TABLE IF NOT EXISTS defense_security.Military_Cyber_Commands (id INT PRIMARY KEY, command_name VARCHAR(255), type VARCHAR(255));INSERT INTO defense_security.Military_Cyber_Commands (id, command_name, type) VALUES (1, 'USCYBERCOM', 'Defensive Cyber Operations'), (2, 'JTF-CND', 'Offensive Cyber Operations'), (3, '10th Fleet', 'Network Warfare');

Query:
Show the name and type of military cyber commands in the 'Military_Cyber_Commands' table.

Response:

----------------------------------------------------------------------------------------------------
BASELINE HUMAN ANSWER:
SELECT command_name, type FROM defense_security.Military_Cyber_Commands;

----------------------------------------------------------------------------------------------------
MODEL GENERATION - ZERO SHOT:
USCYBERCOM, JTF-CND, Offensive Cyber Op

In [13]:
import math

try:
    logger.info("Attempting to load the fine-tuned model...")
    finetuned_model = AutoModelForSeq2SeqLM.from_pretrained("text2sql_flant5base_finetuned")
    tokenizer = AutoTokenizer.from_pretrained("google/flan-t5-base")
    finetuned_model = finetuned_model.to(device)
    to_train = False
    logger.info("Fine-tuned model loaded successfully.")
except Exception as e:
    logger.info("Fine-tuned model not found.")
    logger.info("Initializing model and tokenizer for QLORA fine-tuning...")
    to_train = True

    quant_config = BitsAndBytesConfig(
        load_in_4bit=True,
        bnb_4bit_quant_type="nf4",
        bnb_4bit_use_double_quant=True,
        bnb_4bit_compute_dtype=torch.bfloat16,
    )

    finetuned_model = AutoModelForSeq2SeqLM.from_pretrained(
        model_name,
        quantization_config=quant_config,
        device_map="auto",
        torch_dtype=torch.bfloat16,
    )
    finetuned_model = prepare_model_for_kbit_training(finetuned_model)
    
    lora_config = LoraConfig(
        r=32,
        lora_alpha=64,
        target_modules=["q", "v"],
        lora_dropout=0.1,
        bias="none",
        task_type="SEQ_2_SEQ_LM"
    )
    finetuned_model = get_peft_model(finetuned_model, lora_config)
    tokenizer = AutoTokenizer.from_pretrained(model_name)
    logger.info("Base model loaded and prepared for QLORA fine-tuning.")
    clear_memory()

if to_train:
    output_dir = f"./sql-training-{int(time.time())}"
    logger.info("Starting training. Output directory: %s", output_dir)

    # Compute total training steps:
    num_train_samples = len(tokenized_datasets["train"])
    per_device_train_batch_size = 64
    per_device_eval_batch_size = 64
    num_train_epochs = 6
    # Assuming no gradient accumulation beyond the per-device batch size
    total_steps = math.ceil(num_train_samples / per_device_train_batch_size) * num_train_epochs
    # Set warmup steps as 10% of total steps (adjust as needed)
    warmup_steps = int(total_steps * 0.1)
    
    logger.info("Total training steps: %d, Warmup steps (10%%): %d", total_steps, warmup_steps)
    
    training_args = TrainingArguments(
        output_dir=output_dir,
        gradient_checkpointing=True,
        gradient_checkpointing_kwargs={"use_reentrant": True},
        gradient_accumulation_steps = 2,
        learning_rate=2e-4,
        optim="adamw_bnb_8bit",  # Memory-efficient optimizer
        num_train_epochs=num_train_epochs,
        per_device_train_batch_size=per_device_train_batch_size,
        per_device_eval_batch_size=per_device_eval_batch_size,
        weight_decay=0.01,
        logging_steps=200, 
        logging_dir=f"{output_dir}/logs",
        eval_strategy="epoch",  # Evaluate at the end of each epoch
        save_strategy="epoch",  # Save the model at the end of each epoch
        save_total_limit=3,
        load_best_model_at_end=True,
        metric_for_best_model="eval_loss",
        bf16=True,  
        warmup_ratio=0.1,  # Warmup 10% of total steps
        lr_scheduler_type="cosine",
    )
    trainer = Trainer(
        model=finetuned_model,
        args=training_args,
        train_dataset=tokenized_datasets["train"],
        eval_dataset=tokenized_datasets["validation"],
        callbacks=[EarlyStoppingCallback(early_stopping_patience=2)],
    )
    logger.info("Beginning fine-tuning...")
    trainer.train()
    logger.info("Training completed.")
    save_path = "text2sql_flant5base_finetuned"
    finetuned_model.save_pretrained(save_path)
    logger.info("Model saved to %s", save_path)
    clear_memory()

2025-03-19 15:01:30,827 - INFO - Attempting to load the fine-tuned model...
2025-03-19 15:01:32,195 - INFO - Fine-tuned model loaded successfully.


In [14]:
import logging
import re
import pandas as pd
from rapidfuzz import fuzz
import evaluate

# Assuming tokenizer, device, original_model, finetuned_model, and dataset are already defined.
# Define a helper function for output post-processing.
def post_process_output(output_text: str) -> str:
    """Post-process the generated output to remove repeated text."""
    # Keep only the first valid SQL query (everything before the first semicolon)
    return output_text.split(";")[0] + ";" if ";" in output_text else output_text

# Define a helper function for generating outputs with the given generation parameters.
def generate_with_params(model, input_ids):
    generated_ids = model.generate(
        input_ids=input_ids,
        max_new_tokens=100, 
        num_beams=5,
        repetition_penalty=1.2,
        temperature=0.1,
        early_stopping=True
    )
    # Decode and post-process output
    output_text = tokenizer.decode(generated_ids[0], skip_special_tokens=True)
    return output_text

# Helper functions for SQL normalization and evaluation metrics
def normalize_sql(sql):
    """Normalize SQL by stripping whitespace and lowercasing."""
    return " ".join(sql.strip().lower().split())

def compute_exact_match(predictions, references):
    """Computes the exact match accuracy after normalization."""
    matches = sum(1 for pred, ref in zip(predictions, references)
                  if normalize_sql(pred) == normalize_sql(ref))
    return (matches / len(predictions)) * 100 if predictions else 0

def compute_fuzzy_match(predictions, references):
    """Computes a soft matching score using token_set_ratio from rapidfuzz."""
    scores = [fuzz.token_set_ratio(pred, ref) for pred, ref in zip(predictions, references)]
    return sum(scores) / len(scores) if scores else 0

# Dummy function to free up memory if needed.
def clear_memory():
    # If using torch.cuda, you can clear cache:
    # torch.cuda.empty_cache()
    pass

logger = logging.getLogger(__name__)
logger.setLevel(logging.INFO)

# --- Part A: Inference on 5 Examples with Real Responses ---
logger.info("Running inference on 5 examples (displaying real responses).")

num_examples = 5
sample_queries = dataset["test"][:num_examples]["query"]
sample_contexts = dataset["test"][:num_examples]["context"]
sample_human_responses = dataset["test"][:num_examples]["response"]

print("\n" + "=" * 100)
for idx in range(num_examples):
    prompt = f"""Context:
{sample_contexts[idx]}

Query:
{sample_queries[idx]}

Response:
"""
    # Tokenize the prompt and move to device
    inputs = tokenizer(prompt, return_tensors="pt", truncation=True, max_length=512).to(device)
    
    # Generate outputs using the modified generation parameters
    orig_out = generate_with_params(original_model, inputs["input_ids"])
    finetuned_out = post_process_output(generate_with_params(finetuned_model, inputs["input_ids"]))
    
    print("-" * 100)
    print(f"Example {idx+1}")
    print("-" * 100)
    print("INPUT PROMPT:")
    print(prompt)
    print("-" * 100)
    print("HUMAN RESPONSE:")
    print(sample_human_responses[idx])
    print("-" * 100)
    print("ORIGINAL MODEL OUTPUT:")
    print(orig_out)
    print("-" * 100)
    print("FINE-TUNED MODEL OUTPUT:")
    print(finetuned_out)
    print("=" * 100 + "\n")
    clear_memory()

# --- Part B: Evaluation on Full Test Set with Batching (Optimized) ---
logger.info("Starting evaluation on the full test set using batching.")

all_human_responses = []
all_original_responses = []
all_finetuned_responses = []

batch_size = 128  # Adjust based on GPU memory
test_dataset = dataset["test"]

for i in range(0, len(test_dataset), batch_size):
    # Slicing the dataset returns a dict of lists
    batch = test_dataset[i:i + batch_size]
    
    # Construct prompts for each example in the batch
    prompts = [
        f"Context:\n{batch['context'][j]}\n\nQuery:\n{batch['query'][j]}\n\nResponse:"
        for j in range(len(batch["context"]))
    ]
    
    # Extend human responses
    all_human_responses.extend(batch["response"])
    
    # Tokenize the batch of prompts with padding and truncation
    inputs = tokenizer(prompts, return_tensors="pt", padding=True, truncation=True, max_length=512).to(device)
    
    # Generate outputs for the batch for both models
    orig_ids = original_model.generate(
        input_ids=inputs["input_ids"],
        max_new_tokens=100,
        num_beams=5,
        repetition_penalty=1.2,
        temperature=0.1,
        early_stopping=True
    )
    finetuned_ids = finetuned_model.generate(
        input_ids=inputs["input_ids"],
        max_new_tokens=100,
        num_beams=5,
        repetition_penalty=1.2,
        temperature=0.1,
        early_stopping=True
    )
    
    # Decode and post-process each sample in the batch
    orig_texts = [tokenizer.decode(ids, skip_special_tokens=True) for ids in orig_ids]
    finetuned_texts = [post_process_output(tokenizer.decode(ids, skip_special_tokens=True)) for ids in finetuned_ids]
    
    all_original_responses.extend(orig_texts)
    all_finetuned_responses.extend(finetuned_texts)
    clear_memory()

# Create a DataFrame for a quick comparison of results
zipped_all = list(zip(all_human_responses, all_original_responses, all_finetuned_responses))
df_full = pd.DataFrame(zipped_all, columns=["Human Response", "Original Model Output", "Fine-Tuned Model Output"])
df_full.to_csv('evaluation_results.csv', index=False)
clear_memory()

# --- Compute Evaluation Metrics ---
rouge = evaluate.load("rouge")
bleu = evaluate.load("bleu")

# Compute metrics for the original (non-fine-tuned) model
orig_rouge = rouge.compute(
    predictions=all_original_responses,
    references=all_human_responses,
    use_aggregator=True,
    use_stemmer=True,
)
orig_bleu = bleu.compute(
    predictions=all_original_responses,
    references=[[ref] for ref in all_human_responses]
)
orig_fuzzy = compute_fuzzy_match(all_original_responses, all_human_responses)
orig_exact = compute_exact_match(all_original_responses, all_human_responses)

# Compute metrics for the fine-tuned model
finetuned_rouge = rouge.compute(
    predictions=all_finetuned_responses,
    references=all_human_responses,
    use_aggregator=True,
    use_stemmer=True,
)
finetuned_bleu = bleu.compute(
    predictions=all_finetuned_responses,
    references=[[ref] for ref in all_human_responses]
)
finetuned_fuzzy = compute_fuzzy_match(all_finetuned_responses, all_human_responses)
finetuned_exact = compute_exact_match(all_finetuned_responses, all_human_responses)

print("\n" + "=" * 100)
print("Evaluation Metrics:")
print("=" * 100)
print("ORIGINAL MODEL:")
print(f"  ROUGE: {orig_rouge}")
print(f"  BLEU: {orig_bleu}")
print(f"  Fuzzy Match Score: {orig_fuzzy:.2f}%")
print(f"  Exact Match Accuracy: {orig_exact:.2f}%\n")
print("FINE-TUNED MODEL:")
print(f"  ROUGE: {finetuned_rouge}")
print(f"  BLEU: {finetuned_bleu}")
print(f"  Fuzzy Match Score: {finetuned_fuzzy:.2f}%")
print(f"  Exact Match Accuracy: {finetuned_exact:.2f}%")
print("=" * 100)
clear_memory()

2025-03-19 15:01:32,235 - INFO - Running inference on 5 examples (displaying real responses).
/venv/main/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:629: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(



----------------------------------------------------------------------------------------------------
Example 1
----------------------------------------------------------------------------------------------------
INPUT PROMPT:
Context:
CREATE SCHEMA IF NOT EXISTS defense_security;CREATE TABLE IF NOT EXISTS defense_security.Military_Cyber_Commands (id INT PRIMARY KEY, command_name VARCHAR(255), type VARCHAR(255));INSERT INTO defense_security.Military_Cyber_Commands (id, command_name, type) VALUES (1, 'USCYBERCOM', 'Defensive Cyber Operations'), (2, 'JTF-CND', 'Offensive Cyber Operations'), (3, '10th Fleet', 'Network Warfare');

Query:
Show the name and type of military cyber commands in the 'Military_Cyber_Commands' table.

Response:

----------------------------------------------------------------------------------------------------
HUMAN RESPONSE:
SELECT command_name, type FROM defense_security.Military_Cyber_Commands;
------------------------------------------------------------------

2025-03-19 15:01:40,448 - INFO - Starting evaluation on the full test set using batching.


----------------------------------------------------------------------------------------------------
Example 5
----------------------------------------------------------------------------------------------------
INPUT PROMPT:
Context:
CREATE TABLE WindFarms (FarmID INT, FarmName VARCHAR(255), Capacity DECIMAL(5,2), Country VARCHAR(255)); INSERT INTO WindFarms (FarmID, FarmName, Capacity, Country) VALUES (1, 'WindFarm1', 150, 'USA'), (2, 'WindFarm2', 200, 'Canada'), (3, 'WindFarm3', 120, 'Mexico');

Query:
List the total installed capacity of wind farms in the WindEnergy schema for each country?

Response:

----------------------------------------------------------------------------------------------------
HUMAN RESPONSE:
SELECT Country, SUM(Capacity) as TotalCapacity FROM WindFarms GROUP BY Country;
----------------------------------------------------------------------------------------------------
ORIGINAL MODEL OUTPUT:
1, 150, USA, 2, 200, Canada, 3, 120, Mexico
---------------------

2025-03-19 16:47:58,173 - INFO - Using default tokenizer.
2025-03-19 16:49:07,668 - INFO - Using default tokenizer.



Evaluation Metrics:
ORIGINAL MODEL:
  ROUGE: {'rouge1': np.float64(0.05646642898660111), 'rouge2': np.float64(0.01562815013068162), 'rougeL': np.float64(0.05031267225420556), 'rougeLsum': np.float64(0.05036072587316542)}
  BLEU: {'bleu': 0.003142147128241449, 'precisions': [0.12293406776920406, 0.03289697910893642, 0.018512080104175887, 0.008342750223825794], 'brevity_penalty': 0.11177079327444009, 'length_ratio': 0.3133514352662089, 'translation_length': 377251, 'reference_length': 1203923}
  Fuzzy Match Score: 13.98%
  Exact Match Accuracy: 0.00%

FINE-TUNED MODEL:
  ROUGE: {'rouge1': np.float64(0.7538800834024002), 'rouge2': np.float64(0.6103863808522726), 'rougeL': np.float64(0.7262841884754194), 'rougeLsum': np.float64(0.7261852209847466)}
  BLEU: {'bleu': 0.4719774431701209, 'precisions': [0.7603153442288385, 0.598309257795389, 0.5021259810303533, 0.42128998564638875], 'brevity_penalty': 0.8474086962179814, 'length_ratio': 0.8579477258927689, 'translation_length': 1032903, 'refe

In [15]:
import torch
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer
import logging

# Set up logging
logging.basicConfig(
    level=logging.INFO,
    format="%(asctime)s - %(levelname)s - %(message)s",
)
logger = logging.getLogger(__name__)

# Ensure device is set (GPU if available)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load the fine-tuned model and tokenizer
model_name = "text2sql_flant5base_finetuned" 
finetuned_model = AutoModelForSeq2SeqLM.from_pretrained(model_name, torch_dtype=torch.bfloat16)
tokenizer = AutoTokenizer.from_pretrained("google/flan-t5-base")
finetuned_model.to(device)

def run_inference(prompt_text: str) -> str:
    """
    Runs inference on the fine-tuned model using deterministic decoding
    with beam search, returning the generated SQL query.
    """
    inputs = tokenizer(prompt_text, return_tensors="pt").to(device)
    generated_ids = finetuned_model.generate(
        input_ids=inputs["input_ids"],
        max_new_tokens=100,   # Adjust based on query complexity
        temperature=0.1,      # Deterministic output
        num_beams=5,          # Beam search for better output quality
        early_stopping=True,  # Stop early if possible
    )
    generated_sql = tokenizer.decode(generated_ids[0], skip_special_tokens=True)

    # Post-processing to remove repeated text
    generated_sql = generated_sql.split(";")[0] + ";"  # Keep only the first valid SQL query

    return generated_sql

# Sample context and query (example)
context = (
    "CREATE TABLE customers (id INT PRIMARY KEY, name VARCHAR(100), country VARCHAR(50)); "
    "CREATE TABLE orders (order_id INT PRIMARY KEY, customer_id INT, total_amount DECIMAL(10,2), "
    "order_date DATE, FOREIGN KEY (customer_id) REFERENCES customers(id)); "
    "INSERT INTO customers (id, name, country) VALUES (1, 'Alice', 'USA'), (2, 'Bob', 'UK'), "
    "(3, 'Charlie', 'Canada'), (4, 'David', 'USA'); "
    "INSERT INTO orders (order_id, customer_id, total_amount, order_date) VALUES "
    "(101, 1, 500, '2024-01-15'), (102, 2, 300, '2024-01-20'), "
    "(103, 1, 700, '2024-02-10'), (104, 3, 450, '2024-02-15'), "
    "(105, 4, 900, '2024-03-05');"
)
query = (
    "Retrieve the total order amount for each customer, showing only customers from the USA, "
    "and sort the result by total order amount in descending order."
)

# Construct the prompt
sample_prompt = f"""Context:
{context}

Query:
{query}

Response:
"""

logger.info("Running inference with deterministic decoding and beam search.")
generated_sql = run_inference(sample_prompt)

# Print output in the given format
print("Prompt:")
print("Context:")
print(context)
print("\nQuery:")
print(query)
print("\nResponse:")
print(generated_sql)


2025-03-19 16:51:05,225 - INFO - Running inference with deterministic decoding and beam search.


Prompt:
Context:
CREATE TABLE customers (id INT PRIMARY KEY, name VARCHAR(100), country VARCHAR(50)); CREATE TABLE orders (order_id INT PRIMARY KEY, customer_id INT, total_amount DECIMAL(10,2), order_date DATE, FOREIGN KEY (customer_id) REFERENCES customers(id)); INSERT INTO customers (id, name, country) VALUES (1, 'Alice', 'USA'), (2, 'Bob', 'UK'), (3, 'Charlie', 'Canada'), (4, 'David', 'USA'); INSERT INTO orders (order_id, customer_id, total_amount, order_date) VALUES (101, 1, 500, '2024-01-15'), (102, 2, 300, '2024-01-20'), (103, 1, 700, '2024-02-10'), (104, 3, 450, '2024-02-15'), (105, 4, 900, '2024-03-05');

Query:
Retrieve the total order amount for each customer, showing only customers from the USA, and sort the result by total order amount in descending order.

Response:
SELECT customer_id, SUM(total_amount) as total_amount FROM orders JOIN customers ON orders.customer_id = customers.id WHERE customers.country = 'USA' GROUP BY customer_id ORDER BY total_amount DESC;


In [16]:
import torch
import json
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer
from peft import PeftModel

# Define paths
base_model_name = "google/flan-t5-base"  # Base model name
lora_model_path = "text2sql_flant5base_finetuned"  # Folder where LoRA adapter is saved
full_model_output_path = "text2sql_flant5base_finetuned_full"  # For merged full model

# Load base model and tokenizer
base_model = AutoModelForSeq2SeqLM.from_pretrained(base_model_name, torch_dtype=torch.bfloat16)
tokenizer = AutoTokenizer.from_pretrained(base_model_name)

# Load fine-tuned LoRA adapter model
lora_model = PeftModel.from_pretrained(base_model, lora_model_path)

# ✅ Save the LoRA adapter separately (for users who want lightweight adapters)
lora_model.save_pretrained(lora_model_path)
tokenizer.save_pretrained(lora_model_path)

# ✅ Merge LoRA into the base model to create a fully fine-tuned model
merged_model = lora_model.merge_and_unload()

# ✅ Save the full fine-tuned model
merged_model.save_pretrained(full_model_output_path)
tokenizer.save_pretrained(full_model_output_path)

# ✅ Save generation config (optional but recommended for inference settings)
generation_config = {
    "max_new_tokens": 100,
    "temperature": 0.1,
    "num_beams": 5,
    "early_stopping": True
}
with open(f"{full_model_output_path}/generation_config.json", "w") as f:
    json.dump(generation_config, f)

print(f"✅ LoRA adapter saved at: {lora_model_path}")
print(f"✅ Fully merged fine-tuned model saved at: {full_model_output_path}")


✅ LoRA adapter saved at: text2sql_flant5base_finetuned
✅ Fully merged fine-tuned model saved at: text2sql_flant5base_finetuned_full


In [ ]:
import torch
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer
import logging

# Set up logging
logging.basicConfig(level=logging.INFO, format="%(asctime)s - %(levelname)s - %(message)s")
logger = logging.getLogger(__name__)

# Ensure device is set (GPU if available)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load the fine-tuned model and tokenizer
model_name = "aarohanverma/text2sql-flan-t5-base-qlora-finetuned"
model = AutoModelForSeq2SeqLM.from_pretrained(model_name, torch_dtype=torch.bfloat16).to(device)
tokenizer = AutoTokenizer.from_pretrained("aarohanverma/text2sql-flan-t5-base-qlora-finetuned")

# Ensure decoder start token is set
if model.config.decoder_start_token_id is None:
    model.config.decoder_start_token_id = tokenizer.pad_token_id

def run_inference(prompt_text: str) -> str:
    """
    Runs inference on the fine-tuned model using beam search with fixes for repetition.
    """
    inputs = tokenizer(prompt_text, return_tensors="pt", truncation=True, max_length=512).to(device)

    generated_ids = model.generate(
        input_ids=inputs["input_ids"],
        decoder_start_token_id=model.config.decoder_start_token_id, 
        max_new_tokens=100,  
        temperature=0.1, 
        num_beams=5, 
        repetition_penalty=1.2,  
        early_stopping=True,  
    )

    generated_sql = tokenizer.decode(generated_ids[0], skip_special_tokens=True)

    # Post-processing to remove repeated text
    generated_sql = generated_sql.split(";")[0] + ";"  # Keep only the first valid SQL query

    return generated_sql

# Example usage:
context = (
    "CREATE TABLE employees (id INT PRIMARY KEY, name VARCHAR(100), department VARCHAR(50), salary INT); "
    "CREATE TABLE projects (project_id INT PRIMARY KEY, project_name VARCHAR(100), budget INT); "
    "CREATE TABLE employee_projects (employee_id INT, project_id INT, role VARCHAR(50), "
    "FOREIGN KEY (employee_id) REFERENCES employees(id), FOREIGN KEY (project_id) REFERENCES projects(project_id)); "
    "INSERT INTO employees (id, name, department, salary) VALUES "
    "(1, 'Alice', 'Engineering', 90000), (2, 'Bob', 'Marketing', 70000), "
    "(3, 'Charlie', 'Engineering', 95000), (4, 'David', 'HR', 60000), (5, 'Eve', 'Engineering', 110000); "
    "INSERT INTO projects (project_id, project_name, budget) VALUES "
    "(101, 'AI Research', 500000), (102, 'Marketing Campaign', 200000), (103, 'Cloud Migration', 300000); "
    "INSERT INTO employee_projects (employee_id, project_id, role) VALUES "
    "(1, 101, 'Lead Engineer'), (2, 102, 'Marketing Specialist'), (3, 101, 'Engineer'), "
    "(4, 103, 'HR Coordinator'), (5, 101, 'AI Scientist');"
)

query = ("Find the names of employees who are working on the 'AI Research' project along with their roles.")



# Construct the prompt
sample_prompt = f"""Context:
{context}

Query:
{query}

Response:
"""

logger.info("Running inference with beam search decoding.")
generated_sql = run_inference(sample_prompt)

print("Prompt:")
print("Context:")
print(context)
print("\nQuery:")
print(query)
print("\nResponse:")
print(generated_sql)

/venv/main/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:629: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`. This was detected when initializing the generation config instance, which means the corresponding file may hold incorrect parameterization and should be fixed.
  warnings.warn(
/venv/main/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:629: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
2025-03-19 16:51:49,933 - INFO - Running inference with beam search decoding.
